In [2]:
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib as mpl
from mplsoccer.pitch import Pitch, VerticalPitch
import ipywidgets as widgets
import numpy as np
from matplotlib.colors import LinearSegmentedColormap
import seaborn as sns
from highlight_text import  ax_text, fig_text

#Read in the data
df = pd.read_csv('Footballdata/Others/Napoli/Napoli.csv', encoding='latin-1', low_memory=False)

#Calculating defensive actions in the final third
df = df.loc[(df['x'] > 66.7)]

#Adjust for pitch size
df['x'] = df['x']*1.2
df['y'] = df['y']*.8
df['endX'] = df['endX']*1.2
df['endY'] = df['endY']*.8

#Remove tackles that lose possession
df = df.loc[~((df['type_displayName'] == 'Tackle') & (df['outcomeType_displayName'] == 'Unsuccessful'))]

#Retrieve Team
team = 'Napoli'

#List down relevant defensive actions
list1 = ["Interception","Tackle","BallRecovery",'BlockedPass']

#Filter for defensive actions only
df1 = df[(df['type_displayName'].isin(list1)) & (df['teamId'] == team)]

#df1

In [3]:
#Categorize all of the defensive actions using 'successful' dataframe (Except for Foul)
Recoverydf = df1.loc[(df1['type_displayName'] == "BallRecovery")]
Recoverycount = len(Recoverydf.index)

Interceptiondf = df1.loc[(df1['type_displayName'] == "Interception") | (df1['type_displayName'] == "BlockedPass")]
Interceptioncount = len(Interceptiondf.index)

Tackledf = df1.loc[df1['type_displayName'] == "Tackle"]
Tacklecount = len(Tackledf.index)

In [4]:
recovery_list = Recoverydf.groupby(['playername','teamId']).size().reset_index().rename(columns={0:'Recovery'}).sort_values('Recovery', ascending = False).reset_index()
del recovery_list['index']


interception_list = Interceptiondf.groupby(['playername','teamId']).size().reset_index().rename(columns={0:'Interception'}).sort_values('Interception', ascending = False).reset_index()
del interception_list['index']

tackle_list = Tackledf.groupby(['playername','teamId']).size().reset_index().rename(columns={0:'Tackle'}).sort_values('Tackle', ascending = False).reset_index()
del tackle_list['index']


recovery_list

playername  teamId  Recovery
0   AndrÃ©-Frank Zambo Anguissa  Napoli        36
1         Khvicha Kvaratskhelia  Napoli        34
2                Victor Osimhen  Napoli        24
3             Stanislav Lobotka  Napoli        17
4           Giovanni Di Lorenzo  Napoli        15
5               Piotr Zielinski  Napoli        15
6                Hirving Lozano  Napoli        12
7               Matteo Politano  Napoli        10
8                   Eljif Elmas  Napoli         8
9                    MÃ¡rio Rui  Napoli         8
10             Giovanni Simeone  Napoli         5
11             MathÃ­as Olivera  Napoli         5
12            Giacomo Raspadori  Napoli         4
13            Tanguy NdombÃ©lÃ©  Napoli         2
14                  Diego Demme  Napoli         1
15               Leo ÃstigÃ¥rd  Napoli         1
16               Alessio Zerbin  Napoli         1

In [5]:
#Set up pitch
mpl.rcParams['figure.dpi'] = 500
pitch = VerticalPitch(pitch_type='statsbomb', 
                  pitch_color='#000000', line_color='white',half = True,
                  line_zorder=-3, linewidth=8, spot_scale=0.003)

fig,ax = pitch.draw(figsize=(30, 20), constrained_layout=False, tight_layout=True)
fig.set_facecolor('#000000')

#Inverse the y-axis
plt.gca().invert_xaxis()

pitch.scatter(Tackledf.x,Tackledf.y, marker='o', s=4000, alpha=0.8,
              c='#1d9bf0', edgecolor='w', linewidth=6, ax=ax)

pitch.scatter(Interceptiondf.x,Interceptiondf.y, marker='H', s=4000, alpha=0.8,
              c='red', edgecolor='w',linewidth=6, ax=ax)

"""
pitch.scatter(Recoverydf.x,Recoverydf.y, marker=(5,1), s=5000, alpha=0.95,
              c='#008140', edgecolor='w',linewidth=5, ax=ax)
"""
#Title & Annotations
fig.suptitle("\n\n" + team + "'s\nPossession Won in Final Third\n\n", fontsize=70, color='yellow',
            fontfamily = "Courier New", fontweight = "bold",y=0.95)

highlight_textprops =\
    [{"color": "#1d9bf0","fontweight": 'bold'},
     {"color": "red","fontweight": 'bold'}]

Title = fig_text(s = "<Tackles Won:> " + str(Tacklecount) + " | <Interceptions:> " + str(Interceptioncount),
        x = 0.5, y = 0.74, highlight_textprops = highlight_textprops ,color='white',
        fontfamily = "Courier New",fontweight='bold', ha='center',fontsize=55)

#Space
ax.text(-4, 70, 'space', va='center', ha='left', fontsize=25, color='black',
        fontweight = "bold",fontfamily = "Courier New")

ax.text(89, 70, 'space', va='center', ha='left', fontsize=25, color='black',
        fontweight = "bold",fontfamily = "Courier New")

#Draw line
ax.plot([0,80], [79, 79], c='yellow', lw=9, ls='--')

#shade
plt.axhspan(79,119.9,xmin=0.05,xmax=0.95, color='lightgrey',zorder=-1,alpha=0.2)

plt.show()